In [1]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from bs4 import BeautifulSoup
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [2]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [8]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "http://"
url = protocol + "indiawater.gov.in/imisreports/Reports/Physical/rpt_RWS_TargetAchievement_S.aspx?"
params = {
    'Rep': 0,
    'RP': 'Y',
    'APP': 'IMIS'
}
for key, value in params.items():
    url = url + "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [4]:
#Find Category Selector
financial_year_selector = "ctl00$ContentPlaceHolder$ddfinyear"
state_selector = "ctl00$ContentPlaceHolder$ddState"
cat_selector = "ctl00$ContentPlaceHolder$ddcat"
detail_checkbox = "ctl00$ContentPlaceHolder$chk_detail"
show_button = "ctl00$ContentPlaceHolder$btnGO"
last_col_head = "ctl00_ContentPlaceHolder_rpt_ctl00_lblnoofhabwithcov75to100popcov"
district_radio = "ctl00_ContentPlaceHolder_ddDivisionCat_0"
district_selector = "ctl00$ContentPlaceHolder$dddistrict"

financial_year = "2017-2018"
year_query = ".//option[@value='" + financial_year + "']"
reset = ".//option[@value='-1']"
cat_reset = ".//option[@value='Total']"

def del_show():
    driver.execute_script("return document.getElementsByName('" + show_button + "')[0].remove()")
def check_show():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, show_button ) ) )
    
def detail_check():
    try:
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, detail_checkbox))
        )
        if not element.is_selected():
            #wait start
            del_show()
            element.click()
            #wait end
            check_show()
    except Exception as e:
        print("Error while checking details: ", e)
        pass

def reset_page():
    
    #Get Page
    driver.get(url)
    
    #Get Page
    driver.get(url)
    
    #wait end
    check_show()
        
    #Select Year
    if (driver.find_element_by_name(financial_year_selector).get_attribute("value") == '-1' ):
        #wait
        time.sleep(1)
        del_show()
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, financial_year_selector))
        )
        element.find_elements_by_xpath(".//option")[-1].click
        #wait end
        check_show()
    #Reset now
    #wait
    time.sleep(1)
    del_show()
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, financial_year_selector))
    )
    element.find_element_by_xpath(reset).click()
    #wait end
    check_show()
    #Select year
    #wait
    time.sleep(1)
    del_show()
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, financial_year_selector))
    )
    element.find_element_by_xpath(year_query).click()
    #wait end
    check_show()

    #Reset State
    #wait
    time.sleep(1)
    if not (driver.find_element_by_name(state_selector).get_attribute("value") == '-1' ):
        #wait
        del_show()
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, state_selector))
        ) 
        element.find_element_by_xpath(reset).click()
        #wait end
        check_show()

    #Reset Category
    #wait
    time.sleep(1)
    if not (driver.find_element_by_name(cat_selector).get_attribute("value") == 'Total' ):
        #wait
        del_show()
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, cat_selector))
        ) 
        element.find_element_by_xpath(cat_reset).click()
        #wait end
        check_show()

    #Checkbox details
    time.sleep(1)
    detail_check()

    #Cick Show Button
    time.sleep(2)
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, show_button))
    )
    element.click()

    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.ID, "tableReportTable"))            
    WebDriverWait(driver, 5).until(element_present)
    time.sleep(2)

#Reset Page
reset_page()

#Get all data Categories
table = driver.find_element_by_id('tableReportTable')
head_cats = table.find_elements_by_xpath(".//thead//tr[@class='evenrowcolor']/th[@colspan='3']")[1:]
sub_cat = table.find_elements_by_xpath(".//tr[@class='oddrowcolor']/th")[:3]

#Get habitation Categories #loop over each head_cat
habit_Categories = []
for x in head_cats:
    habit_Categories.append(x.text)
#Remove not needed cats
habit_Categories = habit_Categories[1:]
print ("Total habit_Categories to scrape data for: ",json.dumps(habit_Categories, sort_keys=True, indent=4))

#Get Sub habitation Categories #loop over each sub_cat
sub_Categories = []
for x in sub_cat:
    sub_Categories.append(x.text)
print ("Total sub_Categories to scrape data for: ",json.dumps(sub_Categories, sort_keys=True, indent=4))
        
#Build Financial Year List
financial_years = driver.find_element_by_name(financial_year_selector)
options = financial_years.find_elements_by_xpath(".//option")
#Delete Total
options = options[1:]
financial_years = {}
#loop over each option
for x in options:
    financial_years[x.get_attribute('value')] = x.text
print ("Total financial_year to scrape data for: ",json.dumps(financial_years, sort_keys=True, indent=4))

#Build Category List
temp_list = driver.find_element_by_name(cat_selector).find_elements_by_xpath(".//option")[1:]
categories = []
#loop over each option
for x in temp_list:
    d = {}
    d['text'] = x.text
    d['value'] = x.get_attribute('value')
    categories.append(d)
del temp_list
print ("Total Categories to scrape data for: ",json.dumps(categories, sort_keys=True, indent=4))

#Build State List
temp_list = driver.find_element_by_name(state_selector).find_elements_by_xpath(".//option")[1:]
states = []
#loop over each option
for x in temp_list:
    d = {}
    d['text'] = x.text
    d['value'] = x.get_attribute('value')
    states.append(d)
    #print("State index:",i,d)
del temp_list
print ("Total States to scrape data for: ",json.dumps(states, sort_keys=True, indent=4))

#Build State Dict
temp_list = driver.find_element_by_name(state_selector).find_elements_by_xpath(".//option")[1:]
state_dict = {}
for x in temp_list:
    state_dict[x.text] = x.get_attribute('value')
del temp_list

#Build State District Dict
driver.implicitly_wait(3) # seconds
state_district_dict = {}
for state in states:
    try:
        state_query = ".//option[@value='" + state['value'] + "']"
        
        #Select State
        #wait
        time.sleep(1)
        del_show()
        try:
            driver.execute_script("return document.getElementsByName('" + district_selector + "')[0].remove()")
        except:
            pass
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, state_selector))
        )
        element.find_element_by_xpath(state_query).click()
        #wait end    
        check_show()
        try:
            WebDriverWait( driver, 3 ).until( EC.visibility_of_element_located( ( By.NAME, district_selector ) ) )
        except:
            #Cick Show Button
            element = WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.NAME, show_button))
            )
            element.click()
            element = WebDriverWait(driver, 2).until(
                EC.visibility_of_element_located((By.ID, district_radio))
            )
            
            element = WebDriverWait(driver, 2).until(
                EC.element_to_be_clickable((By.ID, district_radio))
            )
            element.click()
            WebDriverWait( driver, 5 ).until( EC.visibility_of_element_located( ( By.NAME, district_selector ) ) )
        
        #Build District Dict
        temp_list = driver.find_element_by_name(district_selector).find_elements_by_xpath(".//option")[1:]
        district_dict = {}
        for x in temp_list:
            district_dict[x.text] = x.get_attribute('value')
        del temp_list
        
        #Append to State Dict
        state_district_dict[state['text']] = district_dict
        
    except Exception as e:
        print("Error while Building state_district_dict: ", e)
        pass
driver.implicitly_wait(20) # seconds
print (" State District Index: ",json.dumps(state_district_dict, sort_keys=True, indent=4))

('Total habit_Categories to scrape data for: ', '[\n    "No. Of Habitation With Population Coverage > 0 and < 25%", \n    "No. Of Habitation With Population Coverage >= 25 and < 50%", \n    "No. Of Habitation With Population Coverage >= 50 and < 75%", \n    "No. Of Habitation With Population Coverage >= 75 and < 100%", \n    "No. Of Habitation With 100% Population Coverage"\n]')
('Total sub_Categories to scrape data for: ', '[\n    "As on 01/04/2017", \n    "Target (Selected By State)", \n    "Ach"\n]')
('Total financial_year to scrape data for: ', '{\n    "2009-2010": "2009-2010", \n    "2010-2011": "2010-2011", \n    "2011-2012": "2011-2012", \n    "2012-2013": "2012-2013", \n    "2013-2014": "2013-2014", \n    "2014-2015": "2014-2015", \n    "2015-2016": "2015-2016", \n    "2016-2017": "2016-2017", \n    "2017-2018": "2017-2018"\n}')
('Total Categories to scrape data for: ', '[\n    {\n        "text": "Quality Affected", \n        "value": "WQ"\n    }, \n    {\n        "text": "SC-D

In [ ]:
df = None
cat_i = 1 #Increase to skip Category
cat_i_count = len(categories)
while cat_i < cat_i_count:
    row_category_dict = categories[cat_i]
    row_category = row_category_dict['text']
    cat_key = row_category_dict['value']
    cat_query = ".//option[@value='" + cat_key + "']"
    print("\n\n\nAAAAAAAAA\n Scraping Data ->  For category -> ",cat_key,": ",row_category)

    #Reset Page
    reset_page()
    
    #Select Category
    #wait
    time.sleep(1)
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, cat_selector))
    )
    element.find_element_by_xpath(cat_query).click()

    #Checkbox details
    time.sleep(1)
    detail_check()
    
    #Remove Previous Table if any
    try:
        driver.execute_script('document.getElementById("tableReportTable").remove()')
        time.sleep(.5)
    except:
        pass

    #Cick Show Button
    time.sleep(2)
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, show_button))
    )
    element.click()

    data_for_states = 0
    try:
        #Wait for Table to Load fully
        element_present = EC.presence_of_element_located((By.ID, "tableReportTable"))            
        WebDriverWait(driver, 5).until(element_present)
        time.sleep(2)
        #Build Data State List
        temp_list = driver.find_element_by_id('tableReportTable').find_elements_by_xpath(".//tbody/tr")[:-1]
        data_state_list = []
        i = 0
        for x in temp_list:
            xt = x.find_elements_by_xpath(".//td")[1].text.upper()
            data_state_list.append(xt)
            print("-Data Available in this category -> for State -> ",i,": ",xt)
            i+=1
        del temp_list
        print("-Data Available in this category for Total States: ",len(data_state_list))
        #All done so we have data
        data_for_states = 1
    except:
        print("-No Data found for: ","category",row_category)
        pass
    #Start scraping data for states
    if data_for_states > 0:
        state_i = 17 #Increase to skip states
        state_i_count = len(data_state_list)
        while state_i < state_i_count:
            row_state = data_state_list[state_i]
            state_query = ".//option[@value='" + state_dict[row_state] + "']"
            print("\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ",row_category," -> for State: ",state_i," -> ",row_state)
            
            #Reset Page
            reset_page()

            #Select State
            #wait
            time.sleep(1)
            del_show()
            element = WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.NAME, state_selector))
            )
            element.find_element_by_xpath(state_query).click()
            #wait end    
            check_show()

            #Select Category
            #wait
            time.sleep(1)
            element = WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.NAME, cat_selector))
            )
            element.find_element_by_xpath(cat_query).click()

            #Checkbox details
            time.sleep(1)
            detail_check()

            #Remove Previous Table if any
            try:
                driver.execute_script('document.getElementById("tableReportTable").remove()')
                time.sleep(.5)
            except:
                pass

            #Cick Show Button
            time.sleep(2)
            element = WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.NAME, show_button))
            )
            element.click()
            
            #Check if data loaded at district level
            driver.implicitly_wait(3) # seconds
            try:
                WebDriverWait( driver, 3 ).until( EC.visibility_of_element_located( ( By.NAME, district_selector ) ) )
            except:
                element = WebDriverWait(driver, 2).until(
                    EC.visibility_of_element_located((By.ID, district_radio))
                )

                element = WebDriverWait(driver, 2).until(
                    EC.element_to_be_clickable((By.ID, district_radio))
                )
                element.click()
                WebDriverWait( driver, 5 ).until( EC.visibility_of_element_located( ( By.NAME, district_selector ) ) )
                #Cick Show Button
                time.sleep(2)
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, show_button))
                )
                element.click()
            driver.implicitly_wait(20) # seconds
            
            data_for_districts = 0
            try:
                #Wait for Table to Load fully
                element_present = EC.presence_of_element_located((By.ID, "tableReportTable"))            
                WebDriverWait(driver, 5).until(element_present)
                time.sleep(2)
                #Build Data State List
                temp_list = driver.find_element_by_id('tableReportTable').find_elements_by_xpath(".//tbody/tr")[:-1]
                data_district_list = []
                for x in temp_list:
                    xt = x.find_elements_by_xpath(".//td")[1].text.upper()
                    data_district_list.append(xt)
                    print("--Data Available in this category -> this state -> for District: ",xt)
                del temp_list
                print("-Data Available in this category -> this state -> for Total District: ",len(data_district_list))
                #All done so we have data
                data_for_districts = 1
            except:
                print("-No Data found -> for: ","category",row_category)
                pass
            
            #Start scraping data for Districts
            if data_for_districts > 0:
                for row_district in data_district_list:
                    dist_match = 0
                    try:
                        district_query = ".//option[@value='" + state_district_dict[row_state][row_district] + "']"
                        print("\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ",row_category," -> for State: ",row_state," -> for District: ",row_district)
                        dist_match = 1
                    except:
                        pass
                    if dist_match > 0:
                        def data_table_form():
                            #Reset Page
                            reset_page()

                            #Select State
                            #wait
                            time.sleep(1)
                            del_show()
                            element = WebDriverWait(driver, 10).until(
                                EC.element_to_be_clickable((By.NAME, state_selector))
                            )
                            element.find_element_by_xpath(state_query).click()
                            #wait end    
                            check_show()

                            #Check if data loaded at district level
                            driver.implicitly_wait(3) # seconds
                            try:
                                WebDriverWait( driver, 3 ).until( EC.visibility_of_element_located( ( By.NAME, district_selector ) ) )
                            except:
                                #Cick Show Button
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, show_button))
                                )
                                element.click()
                                #Check District Radio button now
                                element = WebDriverWait(driver, 2).until(
                                    EC.visibility_of_element_located((By.ID, district_radio))
                                )
                                element = WebDriverWait(driver, 2).until(
                                    EC.element_to_be_clickable((By.ID, district_radio))
                                )
                                element.click()
                                WebDriverWait( driver, 5 ).until(
                                    EC.visibility_of_element_located( ( By.NAME, district_selector ) ) 
                                )
                                #Cick Show Button
                                time.sleep(2)
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, show_button))
                                )
                                element.click()
                            driver.implicitly_wait(20) # seconds

                            #Select District
                            #wait
                            time.sleep(2)
                            del_show()
                            element = WebDriverWait(driver, 10).until(
                                EC.element_to_be_clickable((By.NAME, district_selector))
                            )
                            element.find_element_by_xpath(district_query).click()
                            #wait end    
                            check_show()

                            #Select Category
                            #wait
                            time.sleep(1)
                            element = WebDriverWait(driver, 10).until(
                                EC.element_to_be_clickable((By.NAME, cat_selector))
                            )
                            element.find_element_by_xpath(cat_query).click()

                            #Checkbox details
                            time.sleep(1)
                            detail_check()

                            #Remove Previous Table if any
                            try:
                                driver.execute_script('document.getElementById("tableReportTable").remove()')
                                time.sleep(.5)
                            except:
                                pass

                            #Cick Show Button
                            time.sleep(2)
                            element = WebDriverWait(driver, 10).until(
                                EC.element_to_be_clickable((By.NAME, show_button))
                            )
                            element.click()

                        data_table_form()

                        data_for_scraping = 0
                        try:
                            #Wait for Table to Load fully
                            element_present = EC.presence_of_element_located((By.ID, "tableReportTable"))            
                            WebDriverWait(driver, 5).until(element_present)
                            time.sleep(2)
                            data_rows_count = len(driver.find_element_by_id('tableReportTable').find_elements_by_xpath(".//tbody/tr")[:-1])
                            if len(driver.find_element_by_id('tableReportTable').find_elements_by_xpath(".//tbody/tr")[:-1]) > 0:
                                #All done so we have data
                                data_for_scraping = 1
                        except Exception as e:
                            print("-No Data found for this category -> this state -> this District | Error: ",str(e))
                            pass

                        #Start scraping data
                        if data_for_scraping > 0:
                            #Loop over each row                        
                            row = 0
                            while row < data_rows_count and data_for_scraping > 0:
                                data_1 = 0
                                try:
                                    #Wait for Table to Load fully
                                    columns = driver.find_element_by_id('tableReportTable').find_elements_by_xpath(".//tbody/tr")[row].find_elements_by_xpath(".//td")
                                    data_1 = 1
                                except Exception as e:
                                    print("!Encountered Error retrying | Error: ",str(e))
                                    data_table_form()
                                    try:
                                        #Wait for Table to Load fully
                                        element_present = EC.presence_of_element_located((By.ID, "tableReportTable"))            
                                        WebDriverWait(driver, 5).until(element_present)
                                        columns = driver.find_element_by_id('tableReportTable').find_elements_by_xpath(".//tbody/tr")[row].find_elements_by_xpath(".//td")
                                        data_1 = 1
                                    except Exception as e:
                                        data_1 = 0
                                        pass
                                if data_1 > 0:
                                    row_block = columns[1].text.strip()
                                    print("----Scraping Data  ->  For category: ",row_category," -> for State: ",row_state," -> for District: ",row_district," -> for Block: ",row_block)
                                    #Loop over all Data columns
                                    column = len(columns) - 15 #5
                                    for h_cat in habit_Categories:
                                        for s_cat in sub_Categories:
                                            try:
                                                cur_col = driver.find_element_by_id('tableReportTable').find_elements_by_xpath(".//tbody/tr")[row].find_elements_by_xpath(".//td")[column]
                                                cur_col_text = cur_col.text
                                                data_2 = 1
                                            except Exception as e:
                                                print("!Encountered Error Reading Ccolumn | Error: ",str(e))
                                                data_table_form()
                                                try:
                                                    #Wait for Table to Load fully
                                                    element_present = EC.presence_of_element_located((By.ID, "tableReportTable"))            
                                                    WebDriverWait(driver, 5).until(element_present)
                                                    data_2 = 1
                                                except Exception as e:
                                                    data_2 = 0
                                                    print("!Encountered Error while Reading this column ",str(e))
                                                    pass
                                            #Check if Link is clickable otherwise nothing
                                            if data_2 > 0 and ( not (cur_col_text == '0') ) :
                                                #Try to click on link to data
                                                try:
                                                    cur_col.find_element_by_tag_name('a').click()
                                                    #Wait for Table to Load fully
                                                    element_present = EC.presence_of_element_located((By.CLASS_NAME, "lnkPages"))
                                                    WebDriverWait(driver, 30).until(element_present)                        
                                                    data_pages = len(driver.find_elements_by_class_name("lnkPages"))
                                                    #print("-----Total Data Pages: ",data_pages)
                                                    #Testing only 
                                                    #data_pages = 1

                                                    i = 0
                                                    while i < data_pages:        
                                                        driver.execute_script('document.getElementById("tableReportTable").remove()')
                                                        driver.find_elements_by_class_name("lnkPages")[i].click()

                                                        #Wait for Table to Load fully
                                                        element_present = EC.presence_of_element_located((By.ID, "tableReportTable"))
                                                        WebDriverWait(driver, 40).until(element_present)

                                                        #Once Loaded Create DataFrame from Table
                                                        html_table = driver.find_element_by_id('tableReportTable').get_attribute('outerHTML')
                                                        df1 = pd.read_html(html_table, skiprows=0)[0]

                                                        #Put Additional Information
                                                        df1['Financial Year'] = financial_year                                                
                                                        df1['Category'] = row_category
                                                        df1['State'] = row_state
                                                        df1['District'] = row_district
                                                        df1['Block'] = row_block
                                                        df1['Habit Category'] = h_cat                            
                                                        df1['Sub Category'] = s_cat

                                                        #Check if master dataframe is empty then copy otherwise concat new Dataframe
                                                        if df is not None:            
                                                            df = pd.concat([df,df1])
                                                        else:
                                                            df = df1.copy()

                                                        #Next Data Page
                                                        i+=1

                                                    #Go Back to previous page for next column
                                                    driver.execute_script("window.history.go(-1)")

                                                #If Encounters error
                                                except Exception as e:
                                                    print("!Encountered Error Going back | Error: ",str(e))
                                                    data_table_form()
                                                    try:
                                                        #Wait for Table to Load fully
                                                        element_present = EC.presence_of_element_located((By.ID, "tableReportTable"))            
                                                        WebDriverWait(driver, 5).until(element_present)
                                                    except Exception as e:
                                                        data_for_scraping = 0
                                                        print("!Encountered Error while recovering from error Skipping this district ",str(e))
                                                        pass

                                            #Next Column it is loop in subcategory
                                            column+=1
                                        #Loop completed for Habitat category
                                #Loop completed for whole Block
                                row+=1
            #state loop Closes
            state_i+=1
    #Cat Loop Closes
    cat_i+=1

('\n\n\nAAAAAAAAA\n Scraping Data ->  For category -> ', u'SC', ': ', u'SC-Dominated')
('-Data Available in this category -> for State -> ', 0, ': ', u'ANDHRA PRADESH')
('-Data Available in this category -> for State -> ', 1, ': ', u'ARUNACHAL PRADESH')
('-Data Available in this category -> for State -> ', 2, ': ', u'ASSAM')
('-Data Available in this category -> for State -> ', 3, ': ', u'BIHAR')
('-Data Available in this category -> for State -> ', 4, ': ', u'CHHATTISGARH')
('-Data Available in this category -> for State -> ', 5, ': ', u'GUJARAT')
('-Data Available in this category -> for State -> ', 6, ': ', u'HARYANA')
('-Data Available in this category -> for State -> ', 7, ': ', u'HIMACHAL PRADESH')
('-Data Available in this category -> for State -> ', 8, ': ', u'JAMMU & KASHMIR')
('-Data Available in this category -> for State -> ', 9, ': ', u'JHARKHAND')
('-Data Available in this category -> for State -> ', 10, ': ', u'KARNATAKA')
('-Data Available in this category -> for State 

('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'BALANGIR', ' -> for Block: ', u'Saintala')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'BALANGIR', ' -> for Block: ', u'Titilagarh')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'BALANGIR', ' -> for Block: ', u'Tureikela')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'BALASORE')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'BALASORE', ' -> for Block: ', u'Bahanaga')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'BALASORE', ' -> for Block: ', u'Balasore')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', 

('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'CUTTACK', ' -> for Block: ', u'Tangi Choudwar')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'CUTTACK', ' -> for Block: ', u'Tigiria')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'DEBAGARH')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'DEBAGARH', ' -> for Block: ', u'Barkote')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'DEBAGARH', ' -> for Block: ', u'Reamal')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'DEBAGARH', ' -> for Block: ', u'Tileibani')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'SC-Dominated', ' -> f

('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JAGATSINGHAPUR', ' -> for Block: ', u'Raghunathpur')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JAGATSINGHAPUR', ' -> for Block: ', u'Tirtol')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JAJPUR')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JAJPUR', ' -> for Block: ', u'Badachana')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JAJPUR', ' -> for Block: ', u'Bari')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JAJPUR', ' -> for Block: ', u'Binjharpur')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: '

('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'KENDRAPARA', ' -> for Block: ', u'Pattamundai')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'KENDRAPARA', ' -> for Block: ', u'Rajkanika')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'KENDRAPARA', ' -> for Block: ', u'Rajnagar')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'KENDUJHAR')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'KENDUJHAR', ' -> for Block: ', u'Anandapur')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'KENDUJHAR', ' -> for Block: ', u'Banspal')
('----Scraping Data  ->  For category: ', u'SC-Dominated', ' -> for 

...

('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'DIMAPUR', ' -> for Block: ', u'Chumukedima')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'DIMAPUR', ' -> for Block: ', u'Dhansiripar')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'DIMAPUR', ' -> for Block: ', u'Kuhuboto')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'DIMAPUR', ' -> for Block: ', u'Medziphema')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'DIMAPUR', ' -> for Block: ', u'Niuland')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'KIPHIRE')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for 

('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'PHEK', ' -> for Block: ', u'Sekruzu')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'PHEK', ' -> for Block: ', u'Weziho')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'TUENSANG')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'TUENSANG', ' -> for Block: ', u'Chare')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'TUENSANG', ' -> for Block: ', u'Chessore')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAGALAND', ' -> for District: ', u'TUENSANG', ' -> for Block: ', u'Longkhim')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'NAG

('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'ANGUL', ' -> for Block: ', u'Kaniha')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'ANGUL', ' -> for Block: ', u'Kishorenagar')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'ANGUL', ' -> for Block: ', u'Pallahara')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'ANGUL', ' -> for Block: ', u'Talcher')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'BALANGIR')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'BALANGIR', ' -> for Block: ', u'Agalpur')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -

('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'CUTTACK', ' -> for Block: ', u'Baramba')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'CUTTACK', ' -> for Block: ', u'Baranga')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'CUTTACK', ' -> for Block: ', u'Cuttack Sadar')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'CUTTACK', ' -> for Block: ', u'Narasinghpur')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'CUTTACK', ' -> for Block: ', u'Tangi Choudwar')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'CUTTACK', ' -> for Block: ', u'Tigiria')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u

('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JHARSUGUDA')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JHARSUGUDA', ' -> for Block: ', u'Jharsuguda')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JHARSUGUDA', ' -> for Block: ', u'Kirimira')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JHARSUGUDA', ' -> for Block: ', u'Kolabira')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JHARSUGUDA', ' -> for Block: ', u'Laikera')
('----Scraping Data  ->  For category: ', u'ST-Dominated', ' -> for State: ', u'ODISHA', ' -> for District: ', u'JHARSUGUDA', ' -> for Block: ', u'Lakhanpur')
('\n\n\nAAAAAAAAA\n -Scraping Data  ->  For category: ', u'ST-Domin

In [6]:
df

Block      Category District Financial Year  GEN Pop  \
0      Agar  SC-Dominated     AGAR      2017-2018      612   
1      Agar  SC-Dominated     AGAR      2017-2018      332   
2      Agar  SC-Dominated     AGAR      2017-2018      245   
3      Agar  SC-Dominated     AGAR      2017-2018      222   
4      Agar  SC-Dominated     AGAR      2017-2018       91   
5      Agar  SC-Dominated     AGAR      2017-2018      184   
6      Agar  SC-Dominated     AGAR      2017-2018      469   
7      Agar  SC-Dominated     AGAR      2017-2018      727   
8      Agar  SC-Dominated     AGAR      2017-2018      318   
9      Agar  SC-Dominated     AGAR      2017-2018      433   
10     Agar  SC-Dominated     AGAR      2017-2018      485   
11     Agar  SC-Dominated     AGAR      2017-2018      306   
12     Agar  SC-Dominated     AGAR      2017-2018      203   
13     Agar  SC-Dominated     AGAR      2017-2018      843   
14     Agar  SC-Dominated     AGAR      2017-2018      104   
15     Agar  SC-Dominated     AGAR      2017-2018      383   
16     Agar  SC-Dominated     AGAR      2017-2018      303   
17     Agar  SC-Dominated     AGAR      2017-2018      419   
18     Agar  SC-Dominated     AGAR      2017-2018      231   
19     Agar  SC-Dominated     AGAR      2017-2018      319   
20     Agar  SC-Dominated     AGAR      2017-2018     1535   
21     Agar  SC-Dominated     AGAR      2017-2018      787   
22     Agar  SC-Dominated     AGAR      2017-2018      168   
23     Agar  SC-Dominated     AGAR      2017-2018      495   
24     Agar  SC-Dominated     AGAR      2017-2018      361   
25     Agar  SC-Dominated     AGAR      2017-2018      366   
26     Agar  SC-Dominated     AGAR      2017-2018      559   
27     Agar  SC-Dominated     AGAR      2017-2018      118   
28     Agar  SC-Dominated     AGAR      2017-2018      257   
29     Agar  SC-Dominated     AGAR      2017-2018      499   
..      ...           ...      ...            ...      ...   
10  Khordha  SC-Dominated   KHURDA      2017-2018       35   
11  Khordha  SC-Dominated   KHURDA      2017-2018      158   
12  Khordha  SC-Dominated   KHURDA      2017-2018       30   
13  Khordha  SC-Dominated   KHURDA      2017-2018       38   
14  Khordha  SC-Dominated   KHURDA      2017-2018        0   
15  Khordha  SC-Dominated   KHURDA      2017-2018        0   
16  Khordha  SC-Dominated   KHURDA      2017-2018       30   
0   Khordha  SC-Dominated   KHURDA      2017-2018      162   
0     Tangi  SC-Dominated   KHURDA      2017-2018     2500   
1     Tangi  SC-Dominated   KHURDA      2017-2018      122   
2     Tangi  SC-Dominated   KHURDA      2017-2018      116   
3     Tangi  SC-Dominated   KHURDA      2017-2018        1   
0     Tangi  SC-Dominated   KHURDA      2017-2018       76   
1     Tangi  SC-Dominated   KHURDA      2017-2018      288   
2     Tangi  SC-Dominated   KHURDA      2017-2018      382   
0     Tangi  SC-Dominated   KHURDA      2017-2018       36   
1     Tangi  SC-Dominated   KHURDA      2017-2018       90   
2     Tangi  SC-Dominated   KHURDA      2017-2018      273   
3     Tangi  SC-Dominated   KHURDA      2017-2018      288   
4     Tangi  SC-Dominated   KHURDA      2017-2018       53   
5     Tangi  SC-Dominated   KHURDA      2017-2018        5   
6     Tangi  SC-Dominated   KHURDA      2017-2018        7   
7     Tangi  SC-Dominated   KHURDA      2017-2018        9   
8     Tangi  SC-Dominated   KHURDA      2017-2018       40   
9     Tangi  SC-Dominated   KHURDA      2017-2018     1109   
10    Tangi  SC-Dominated   KHURDA      2017-2018       41   
11    Tangi  SC-Dominated   KHURDA      2017-2018       40   
12    Tangi  SC-Dominated   KHURDA      2017-2018        0   
13    Tangi  SC-Dominated   KHURDA      2017-2018     1312   
14    Tangi  SC-Dominated   KHURDA      2017-2018       26   

                                       Habit Category  \
0     No. Of Habitation With 100% Population Coverage   
1     No. Of Habitation With 100% Population Co

In [7]:
#Save Scrapped File
df.to_csv(os.path.join(output_folder, financial_year+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

In [ ]:
#Read Edited File
df = pd.read_csv(os.path.join(output_folder, financial_year+'_Scrapped_Data.csv'), encoding='utf-8')

In [ ]:
#Cleaner

#Reset Index
df = df.reset_index(drop=True)
df = df.drop(columns=['Sl.No.'])

#Get List of Columns to Group
columns = list(df.columns)
columns.remove('Category')

#Create Binary Variables
cat_i = 0 #Increase to skip states
cat_i_count = len(categories)
while cat_i < cat_i_count:
    row_category_dict = categories[cat_i]
    row_category = row_category_dict['text']
    cat_key = row_category_dict['value']
    df[row_category] = 0
    df.loc[df['Category'] == row_category, row_category] = 1
    cat_i+=1
    
#Group the dataframe and sum the binary variables
df = df.fillna(-999).groupby(columns).sum().reset_index()

#Save to file
df.to_csv(os.path.join(output_folder, financial_year+'_Scrapped_Cleaned_Data.csv'), encoding='utf-8', index=False)